In [1]:
!pip install xlrd
!pip install geopandas
!pip install openpyxl
!pip install googletrans
!pip install goslate
!pip install textblob

In [2]:
import pandas as pd
import folium  
import geopandas as gpd

In [3]:
df_airbnb=pd.read_csv('Aribnblocalidades.csv')
g=df_airbnb.groupby(['Nombre_Localidad'])['Average Daily Rate (Native)'].mean().to_frame()
#pd.DataFrame(data=g).rename_axis('index')
g.index.names=['Localidades']
g.reset_index()
g['Average Daily Rate (Native)']=g['Average Daily Rate (Native)'].round(2)

/opt/conda/lib/python3.8/site-packages/IPython/core/interactiveshell.py:3165: DtypeWarning: Columns (5,15,30,42,43,51,52) have mixed types.Specify dtype option on import or set low_memory=False.
  has_raised = await self.run_ast_nodes(code_ast.body, cell_name,


In [4]:
#dic=g.to_dict()
#print(dic)

In [5]:
#Read polygons
#https://www.naturalearthdata.com/downloads/10m-cultural-vectors/10m-admin-0-countries/
shapefile='poligonos-localidades.shp'
gdf=gpd.read_file(shapefile,encoding='UTF-8')[['Nombre_de_l','geometry']]
gdf=gdf.rename(columns={'Nombre_de_l':'Localidades',
                        'geometry':'geometry'
                       }
              )
gdf['Localidades']=gdf['Localidades'].str.lower()
gdf['Localidades']=gdf['Localidades'].str.capitalize()
dic_localidades={'Antonio nariño':'Antonio Nariño',
                'Barrios unidos': 'Barrios Unidos',
                'Engativa':'Engativá',
                 'Fontibon':'Fontibón',
                 'Candelaria':'La Candelaria',
                 'Los martires':'Los Mártires',
                 'Puente aranda':'Puente Aranda',
                'Ciudad bolivar':'Ciudad Bolivar',
                 'Rafael uribe uribe':'Rafael Uribe Uribe',
                 'San cristobal':'San Cristobal',
                 'Santa fe':'Santa Fe',
                 'Usaquen':'Usaquén'
                }
gdf['Localidades']=gdf['Localidades'].replace(dic_localidades)

In [6]:
df=pd.merge(g,gdf, on='Localidades', how='left')

In [7]:
gdf = gpd.read_file('poligonos-localidades.geojson')
#json = gpd.GeoSeries([gdf.geometry.iloc[0]]).__geo_interface__
gdf['Localidades']=gdf['Nombre de la localidad'].str.lower()
gdf['Localidades']=gdf['Localidades'].str.capitalize()
dic_localidades={'Antonio nariño':'Antonio Nariño',
                'Barrios unidos': 'Barrios Unidos',
                'Engativa':'Engativá',
                 'Fontibon':'Fontibón',
                 'Candelaria':'La Candelaria',
                 'Los martires':'Los Mártires',
                 'Puente aranda':'Puente Aranda',
                'Ciudad bolivar':'Ciudad Bolivar',
                 'Rafael uribe uribe':'Rafael Uribe Uribe',
                 'San cristobal':'San Cristobal',
                 'Santa fe':'Santa Fe',
                 'Usaquen':'Usaquén'
                }
gdf['Localidades']=gdf['Localidades'].replace(dic_localidades)
gdf['Hospedajes']=gdf['Localidades']
diccionario={'Antonio Nariño': 69613.07, 'Barrios Unidos': 70591.74, 'Bosa': 56699.67, 'Chapinero': 97563.65, 
             'Ciudad Bolivar': 71321.78, 'Engativá': 74499.99, 'Fontibón': 73374.29, 'Kennedy': 67953.83, 
             'La Candelaria': 75248.05, 'Los Mártires': 68152.14, 'Puente Aranda': 66043.89, 'Rafael Uribe Uribe': 98043.51, 
             'San Cristobal': 62383.77, 'Santa Fe': 75554.95, 'Suba': 81663.73, 'Teusaquillo': 70962.1, 'Tunjuelito': 72434.09,
             'Usaquén': 104097.5, 'Usme': 44.0}
gdf['Hospedajes']=gdf['Hospedajes'].replace(diccionario)

In [8]:
bog_coords = [4.60971,-74.08175]
m = folium.Map(location=bog_coords) # se crea un mapa vacio con coordenadas del centro y se define el zoom con el que se va visualizar
folium.Choropleth(geo_data = gdf, #the geopandas dataframe with the geometries
                 data = df, #the dataframe containing values we want to show in the map
                 columns = ['Localidades','Average Daily Rate (Native)'], #the columns inside the data dataframe that contains the keys and the values to be mapped
                 key_on = 'feature.properties.Localidades', # llave con la cual se va hacer el join con el df
                 fill_color = 'YlGnBu', # YlOrRd 
                 legend_name="Precio Promedio por Noche Airbnb (COP)",
                 nan_fill_color="White",
                 ).add_to(m)
# Crear etiquetas
style_function = lambda x: {'fillColor': '#FFFFFF',
                            'color':'#000000',
                            'fillOpacity': 0.1,
                            'weight': 0.1}
highlight_function = lambda x: {'fillColor': '#000000',
                                'color':'#000000',
                                'fillOpacity': 0.50,
                                'weight': 0.1}
etiquetas = folium.features.GeoJson(
    gdf,
    style_function=style_function,
    control=False,
    highlight_function=highlight_function,
    tooltip=folium.features.GeoJsonTooltip(
        fields=['Nombre de la localidad','Hospedajes'],
        aliases=['Localidad:','Precio promedio Airbnb:'],
        style=('background-color: white; color: #333333; font-family: arial; font-size: 12px; padding: 10px;')
    )
   ).add_to(m)
m

In [9]:
m.save('HeatMapAirbnbPrecios.html')